In [ ]:
#r "nuget: Plotly.NET, 4.2.0"
#r "nuget: Plotly.NET.Interactive, 4.2.0"


# Scatter and line plots on Mapbox maps

[![Binder](https://plotly.net/img/badge-binder.svg)](https://mybinder.org/v2/gh/plotly/plotly.net/gh-pages?urlpath=/tree/home/jovyan/mapbox-map-charts/mapbox-plots.ipynb)&emsp;
[![Notebook](https://plotly.net/img/badge-notebook.svg)](https://plotly.net/mapbox-map-charts/mapbox-plots.ipynb)

**Summary:** This example shows how to create Point and Line charts on Mapbox maps in F#.

Let's first create some data for the purpose of creating example charts:



In [3]:
open Plotly.NET

let cityNames =
    [ "Montreal"
      "Toronto"
      "Vancouver"
      "Calgary"
      "Edmonton"
      "Ottawa"
      "Halifax"
      "Victoria"
      "Winnepeg"
      "Regina" ]

let lon =
    [ -73.57
      -79.24
      -123.06
      -114.1
      -113.28
      -75.43
      -63.57
      -123.21
      -97.13
      -104.6 ]

let lat = [ 45.5; 43.4; 49.13; 51.1; 53.34; 45.24; 44.64; 48.25; 49.89; 50.45 ]


The simplest type of geographic plot using Mapbox is plotting the (lon,lat) pairs of a location via `Chart.PointMapbox`.
Here is an example using the location of Canadian cities:



In [4]:
open Plotly.NET.LayoutObjects

let pointMapbox =
    Chart.PointMapbox(
        longitudes = lon,
        latitudes = lat,
        MultiText = cityNames,
        TextPosition = StyleParam.TextPosition.TopCenter
    )
    |> Chart.withMapbox (Mapbox.init (Style = StyleParam.MapboxStyle.OpenStreetMap, Center = (-104.6, 50.45)))


In [ ]:
pointMapbox


<!-- Plotly chart will be drawn inside this DIV -->

To connect the given (lon,lat) pairs via straight lines, use `Chart.LineGeo`.
Below is an example that pulls external data as a Deedle data
frame containing the source and target locations of American Airlines flights from Feb. 2011:



In [6]:
open Deedle
open System.IO
open System.Text

let data =
    __SOURCE_DIRECTORY__ + "/../data/2011_february_aa_flight_paths.csv"
    |> fun csv -> Frame.ReadCsv(csv, true, separators = ",")

let opacityVals: float[] =
    data.["cnt"]
    |> Series.values
    |> fun s -> s |> Seq.map (fun v -> v / (Seq.max s)) |> Array.ofSeq

let startCoords = Series.zipInner data.["start_lon"] data.["start_lat"]
let endCoords = Series.zipInner data.["end_lon"] data.["end_lat"]
let coords = Series.zipInner startCoords endCoords |> Series.values

let flights =
    coords
    |> Seq.mapi (fun i (startCoords, endCoords) ->
        Chart.LineMapbox(
            lonlat = [ startCoords; endCoords ],
            Opacity = opacityVals.[i],
            LineColor = Color.fromString "red"
        ))
    |> Chart.combine
    |> Chart.withLegend (false)
    |> Chart.withMapbox (Mapbox.init (Style = StyleParam.MapboxStyle.OpenStreetMap, Center = (-97.0372, 32.8959)))
    |> Chart.withMarginSize (0, 0, 50, 0)
    |> Chart.withTitle "Feb. 2011 American Airline flights"


In [ ]:
flights


<!-- Plotly chart will be drawn inside this DIV -->